In [36]:
import psycopg2
import requests
import json
import pandas as pd
import time

In [33]:
MAAS_ENDPOINT = "https://model-service.worldmodelers.com/"
#conn = psycopg2.connect(host="maas.cowfye1azh5f.us-east-1.rds.amazonaws.com",database="output", user="wmuser", password="REPLACEME")
#cur = conn.cursor()
user = "wmuser"
password = "Bq248mEDuUap"

In [18]:
# get all training data (configs + outputs)
def get_training_data(model_name):
    response = requests.get(MAAS_ENDPOINT + "list_runs/" + model_name)
    run_ids = json.loads(response.text)
    
    datas = []
    configs = []
    for rid in run_ids:
        #rid = rid.lower()
        config_response = requests.get(MAAS_ENDPOINT + "run_results/" + rid)
        config = json.loads(config_response.text)        
        statement = f"SELECT * FROM rundata where run_id = '{rid}';"
        cur.execute(statement)
        print(cur.fetchall())
        output_df = pd.DataFrame(cur.fetchall(),columns=['run_id', 'x', 'y','id','feature','datetime'])
        datas.append(output_df)
        configs.append(config)
            
    return configs, datas

In [70]:
np.arange(.0000000011,1.25,.24999999999)

array([  1.10000000e-09,   2.50000001e-01,   5.00000001e-01,
         7.50000001e-01,   1.00000000e+00])

In [72]:
import pandas as pd
import numpy as np
d = pd.read_csv("/Users/jgawrilow/single_shock_results.csv")
countries = list(d.country)
#countries = ["ETH"]
fractional_reserve_access = list(np.arange(.0000000011,1.25,.24999999999))
production_decrease = list(np.arange(.0000000011,1.25,.24999999999))
year = list(range(2005,2010))
mmatrix = list(itertools.product(*[countries,fractional_reserve_access,production_decrease,year]))
print(len(mmatrix))

20750


In [6]:
import itertools
run_matrix = {
    "x":range(0,100),
    "y":["A","B","C"],
    "z":["Z","Y","X"]
}

test = [[1,2,3],[4,5,6]]

result = list(itertools.product(*test))
print(result)

[(1, 4), (1, 5), (1, 6), (2, 4), (2, 5), (2, 6), (3, 4), (3, 5), (3, 6)]


In [65]:
"""
if params are 
-- x float [0-100]
-- y A B C
-- z Z Y Z
"""

run_matrix = {
    "x":range(0,100),
    "y":["A","B","C"],
    "z":["Z","Y","X"]
}

def range_to_list(x):
    vals = []
    k = x.keys()[0]
    for v in x[k]:
        vals.append({k:v})
        
#result = list(itertools.product(*inputdata))
    

# continuously run model and cache outputs
def run_and_cache(session,model_name,runs,fields):
    
    for j, run in enumerate(runs):
        mydata = {
           "config":{},
           "name":model_name
        }
        for i, field in enumerate(fields):
            mydata["config"][field] = run[i]

        URL = MAAS_ENDPOINT + "run_model"
        #print(json.dumps(mydata))
        resp = session.post(URL, json=mydata)
        rid = resp.text.replace('"',"").strip()
        time.sleep(2)
        run_response = session.get(MAAS_ENDPOINT + "run_status/" + rid)
        STATUS = run_response.text.replace('"',"").strip()
        print(j, rid, STATUS)

        while STATUS != "SUCCESS" and STATUS != "FAIL":
            time.sleep(1)
            URL = MAAS_ENDPOINT + "run_status/" + rid
            run_response = session.get(MAAS_ENDPOINT + "run_status/" + rid)
            STATUS = run_response.text.replace('"',"").strip()
            print(i, rid, STATUS)
        
        
        
    

In [25]:
configs, datas = get_training_data("DSSAT")
print(datas)

NameError: name 'get_training_data' is not defined

In [73]:
session = requests.Session()
session.auth = (user, password)
run_and_cache(session,"FSC",mmatrix,["country","fractional_reserve_access","production_decrease","year"])

0 8136826a6f00e351856148195bacc7e6fbc82f8238fdc92bff198dd94ba9bb0b SUCCESS
1 dbbee69ff7ae5d1428251049f468c784daa9db2afaa9653969b98c3d2e2d22a7 SUCCESS
2 723412353ffa785e9bf214f3055db84dc8b2c961d2bbd04bfd41a4336608fc53 SUCCESS
3 f90bdf04df5cf015dad8bd58ce950fb55070c748d6cc69f7bb9f844f7da32d57 SUCCESS
4 fc7b353e1cfce9b33809cfd1faf6bc4a230cb839faeb2c8e451ae6748d56be17 SUCCESS
5 5eb264e4227c15e1801403e91e33a508e7703c862db85692cac93e4324a4a05f SUCCESS
6 7a7447d0984125476dcb62ddc40a58573cd7836e11b2f62415867322c54050c7 SUCCESS
7 881052c5f79761e76468b5eb402938f392e0f9dcfc5bfb3de47b34a6de1e9aaf SUCCESS
8 9e2ade6c4da2faeffdca696413b235e30bf1f8d408ac8c5c5bab42a694710794 SUCCESS
9 f47e7991053abd729278145c973145244b1ed30cefa77691da4cd8d1523f36d4 SUCCESS
10 98673d370dc9695c3cbe4e641481de83b119456a3728bfefea00d0fdc586a937 SUCCESS
11 5a564cd0f650d478056bbf76a661b03bb89c2003be77ebe1e59b446d23f4d757 SUCCESS
12 4f22277de3f3b5b5276435ee5cc1248032a7d420ed5152a0caa702da630dbbd8 SUCCESS
13 0105e62b3a51eafbac6

108 c21f2d85b64756188268d3e74c23244ea906e085571dcfdc674b41d2892d03c3 SUCCESS
109 c819ff36098ba68e44fd7ffad0ed66e0cf132c393a1f2fb6d9681f9d1f53d297 SUCCESS
110 a4eb52562148dc7a16b847f21502b5f2f58d6f61f4f387d6c5d4c4d74ddf63ab SUCCESS
111 5f1131692a4bc30415b2875d0534bc2e5d0c54e47c729711333471b156c8f219 SUCCESS
112 1a9c1e7585a2f508f6d170bd4d95ca31122b136841328d76b74ea7367cc51717 SUCCESS
113 9a2e6bbb4a81e2c15ac446faf38351b81b96f30af7160b9546390b6c262043a0 SUCCESS
114 986bf74296e8f6f64dda6afe4a709d79694764453133b3b1d7299b790fa86495 SUCCESS
115 4e2476920ad3e4116e4d3974706ef7032d8d77963ddeae8410f4c5b1bd3c1d2b SUCCESS
116 19ca81fff7a70ba8b8f48a5c6327e5fd6ec55d801805bc3fed8c64044c55a1a0 SUCCESS
117 3989b0bb650218f029f04d2832540ed9e99d61a55707dfaf083825cf8e723456 SUCCESS
118 e31a36f38465d77428fdf09f30c5d510addb553b8f7f03901e3d23cafc726b7f SUCCESS
119 2d23ae38984344ba38a5ea872b61f087f7b14ca244d8dc5665ccf9700e973709 SUCCESS
120 68e2dabcb9f5357e4a75b0ddbec255b6b1dcf3fdc63ebb33ebf53aaad4da70be SUCCESS

213 3e7af3f8db90eec4d2ef8f96912558bb623fc039d47072a72cde582ba0d76e09 SUCCESS
214 778fa691c80ab498793310365e79a390cb995f740ad79dbeaac0abbf69306e01 SUCCESS
215 9e158b947b4d61adeaa44fe00e90ae59cb1253a45fccd37f54ec1d1333daf97c SUCCESS
216 b45046b072e8f68170538328e415e3de255da1dcd471fdfb4d81ecf7eb7ff11f SUCCESS
217 e0c39283224deaa6d6a00849aa58480ac668be5dd3bc913745009b915b002a52 <html>
<head><title>504 Gateway Time-out</title></head>
<body bgcolor=white>
<center><h1>504 Gateway Time-out</h1></center>
<hr><center>nginx/1.14.0 (Ubuntu)</center>
</body>
</html>
3 e0c39283224deaa6d6a00849aa58480ac668be5dd3bc913745009b915b002a52 SUCCESS
218 e48f667c48ab4456d6b83ef0021a1470ef0effaa240c7998443d24483ba619f8 SUCCESS
219 ad81a8cc1d3d06ae9c13cbfe793b191e28775dff189d8d7780b84726d74797bf SUCCESS
220 e48714c475a204f753b85855212711cc698abee1a635641483741565a753add9 SUCCESS
221 13a5ebc1afadce6e9114d2866ebfd0edc379f15bf8523bfdb3732732f0ee86f9 SUCCESS
222 d17fa65560989f3c0da5db9f279dda4f82c7238a07ac35b319e90

317 142cc094b2096a4e7c0e65bfc1feb01c97ce3029aed91ad940738d0536a464cd SUCCESS
318 e0f547333df288c88222eb5933c2929f6b2e8f17778314df51103f4fc7789649 SUCCESS
319 c313e2e3658c3d9bc0f5eee8bb0bccff39f7597fdb61fd573a8b8e05e50c6bfb SUCCESS
320 4890b405bd04153566ca830db8d4318947a34c96552029b0bfb8bee7fef73314 SUCCESS
321 1b4ad430c6bd09f93da4826f79914e07c5660eae2042a8e7ee4c4ec386c9f78b SUCCESS
322 1896d327831e895d85d54c3dd3ab3a495475a0898b3d71153427257999119bb1 SUCCESS
323 5a3524fa57c2443c6a55a1348295171360611acdd7aa30afaa1d519c8db6448a SUCCESS
324 76052f278485788ec04beb8381b8ea67953d306225314a3e9a1a67370eb37163 SUCCESS
325 053c186351a7b4eb333101f1d7ebc84c5e75f8fe63fd7c4aa33297b5df0c2676 SUCCESS
326 57631f37735508c792226be470dd14894302c28347cd951c9b549bfc79f5b073 SUCCESS
327 ab2f11308fd2c3203ed5ab2a5cd139d41fc8d773f0848e7f2417fcab360c97dd SUCCESS
328 58cb1b9b2356533ef9555787163c892c7c687ef86b8b2bd99aa2a6bb0eee1dbd SUCCESS
329 8486ac5cfab0e06fb0050ee9ce44580133947cddbac5a934a2e39536011cc6de SUCCESS

424 83dc10b1867185e08b69b51688effc314d4d01f14154ff534a66cfead2a18f83 SUCCESS
425 1f727455922de07c95ae96dabfe53a9cd8553915af40e9acb5313e32c620c8af SUCCESS
426 e98cd19bcbd4e2c51d897280e17e8f94a6a51ff7f6781d663ba6c650ad972da8 SUCCESS
427 87d3e56c91be32ad2348fa88247f68295c63ce74c8d21905afffc6908d36e736 SUCCESS
428 48197b6f798783637a0e88ff749262e8f92b29b3e3901afcd56c66e94634f698 SUCCESS
429 6147f3dd46bd07fb0b32c241b73bba8621b6b7be83db1527f15d2b21894fb33b SUCCESS
430 20dd0f8db976cc0809c477045459ef91a46ecda24287760a9f24965530d3e0f1 SUCCESS
431 c08f09b78f96fed8cc35a4e96bcb2faa5c4d6181acb3dbee30729ce6fde30d15 SUCCESS
432 aef955114b674ca5e89de5094c2421d7f548895b4877cb070a0963d8172c3e56 SUCCESS
433 5f0c53efca6f9849775afede48712248e6098f9f4c472eaa60fe7a1a3de58b14 SUCCESS
434 7cf5e35c164296571173c87232267c46b831af11350e43a850ba21c4426bc34d SUCCESS
435 5092491b08c8c3d7e56d1edb4ea5f91676639bb3d37a7380ea0e58385cda540f SUCCESS
436 c0c9875f3725331f4cf9619a64ee1d137a3ca3ffe1fed948f956171813234088 SUCCESS

...

20327 4c99502428da100f5044b42d212cd72f87671659d7353bfc40b9e5fe4e70cf80 SUCCESS
20328 fa8fa4bf38909cbc5985da59eaf066a6bc22ac358dd688a7a4754d65f020a87e SUCCESS
20329 207ee79bac4c0414f01f50730e4d4d625cfc63a5e011ef04cf4ba958ee951350 SUCCESS
20330 23259d66b940e362b37894b5f7500f31558288468d61dc5bd231530b21b0eabc SUCCESS
20331 726226618920313da6ecb50db6c977cee200cc74e9bca1758bb3e35b15d5366e SUCCESS
20332 082f3201262bae0e9da231dce991db1e6044aca9f7316516b18a2d72e5704730 SUCCESS
20333 ec94bd7a12131f4a5ba4219e5419a84aaccbb9eafeeef024599de90c2abe25b6 SUCCESS
20334 d4f8c23cc2b42b3ce628f28997b79ee8fa05243f3285d9928603840bbe3c1181 SUCCESS
20335 995e371da848eb110d374e0001fff1a9dbdd0ae4f6908ed8f2d5551863ace167 SUCCESS
20336 a51fc5ffaedb975644a3d2b59bd0d9cec5156e6f520e08f3a5d9ec56c9d235c3 SUCCESS
20337 af2111f07a8a72f71a1c6d39d23f95c3e598c2b6d4ca23524cf9fd4f946f14e4 SUCCESS
20338 a33364817213682c2ff529e138c82f18ec4d1768b66c1d1df6ca18c41d4833fa SUCCESS
20339 09be6cdb4fd6fbd55eb92eb99eab05f5de067396bb1bd2

20431 bea1b65f5a92c93bde443a8b14692d9f7e970e14d33fe7237bb39fc541244900 SUCCESS
20432 0dd0fcda9ca6086d566c3d217796db89b2f5be443ff255eebac17ae7aba24480 SUCCESS
20433 724e35a0fb7df8b61f73abde32c4034620816833af08fb57a20e51d2a5787886 SUCCESS
20434 e9e6860f0ece933f15b3c5f263a790248a6de95a123f51cff3f306735d182328 SUCCESS
20435 d77c82b8df666f101a9aec22651ab844c94774d7e4947e2548a8aa2e261f2c49 SUCCESS
20436 3507485ec84f92792e4dd61d90ee1eb95b2203f15ade7e6b1e25183f95c688c6 SUCCESS
20437 d5b4a2c4591489abb0f3c6dd8a6d90ab63a347512013a3abd02cfe8e08adfe62 SUCCESS
20438 5f870b5611f72b08b0b4888f5a752c2c96b6235b302cea4e175897856d6a0b7d SUCCESS
20439 43be7c14581952be02f294a769585a6548e2748d2d1b8dd14d715f14ad346d49 SUCCESS
20440 f7d5a179f7815d7fde3f05dc8c73f527ef73a6c0b861286acc3fe89bba02a4c7 SUCCESS
20441 f224a12b83b22ee40331d392ea4f1972db4b0d1ad435c58c4d863cc58c565fd5 SUCCESS
20442 cba3d382c2ca7150f0de27c2ff4da2de31ba02b6cd3e9847d5d77a9170a0906c SUCCESS
20443 bf3d0fe172c978803dff6d94d9143de492073edc0c3e66

20536 a3bfac61b6a18d84a0e85989249664b9321dc044aa544bd2579abd3d51829922 SUCCESS
20537 e3b263d84cc278bba04f1f3a007122f9156369b5ea4f06a4fb4e8f69cf68d387 SUCCESS
20538 21063410ecf78378cf7355c34ce2e89df4957c8ca452fa6743f9999b8c87144e SUCCESS
20539 5705840da602ff25247910b0fb71679040bf1eac79470bfddcd1d8513c7775c6 SUCCESS
20540 4741d48ab376b76120ed0025c4672bc57092bf355007e7296eb98bf8d7bf4658 SUCCESS
20541 fe36a9c7503c22f8f6fe6d598a2139fc325a86993353751868c76dc775e55677 SUCCESS
20542 00fc3e2dd0b7d70fa5536727aee442a4dd47e487f1b6dd4e3d044cb31278c851 SUCCESS
20543 cacd6cb9fe6334a823658630960387e9475e4e4919e5d020ff3767af347e8741 SUCCESS
20544 db0172e5d3effc016fe6b0156b5f6440506ae83b719373cef7193f7dee886156 SUCCESS
20545 9e2c68ffd5cb743e209ddd7fc12529c86991e15e3f3f1e0dd668f0cd08e7b422 SUCCESS
20546 2a14aaccc55ef7527211f9d5a8220cd4330962810319dbd29864c64acce4b5a1 SUCCESS
20547 6e18683ffd9e3f69ee475b673e98518a61073acb4e1b56b20b910a6595f7bf7e SUCCESS
20548 f58c4d333fc2bf13c5cad2bd4e26e9fd9542b9c6e13c9a

20640 aa1515b18b9351773a817cb2ffe074adfae1606b13435ec705e5583a6eeeb0a6 SUCCESS
20641 c1ac1ca19e4cea4f41934868620ea207f78f2677bc440750770e2da2de8c9916 SUCCESS
20642 04322fec0bd4f99eb06dcd9df6011aa504a40493fe7aa394a29b6fb2af72854e FAIL
20643 6efb2f6c64b52fc72209b0ab2e55e31d1f4cc12ed5113767fa78476b4fe03eaf FAIL
20644 090d19464332ce1b8615b433478fb122c009a546250a31a9478be40924b9fd8b SUCCESS
20645 67c2e7b72a32264ba02f9aee7c62692baa07cebb99037a3e4dbf08a5ceef8e4f SUCCESS
20646 8618d17438796e4a99d63e4dd3b270a42833dc26fae81e3b1bf2d00e6b709b95 SUCCESS
20647 a825be7312f911e836e973a66fa5d5658b557062bb595ee99ff9b1f6074ff513 FAIL
20648 19115926571dae9060f4ef00db448693f3e3bb602a238b745f2b6aad28dbfcdb FAIL
20649 dec6cfbe89e9a51bc72d9d40bf4ebafea61d915d4129a31082c0868f85aea270 SUCCESS
20650 a1c29f650f96ca4a85062196a5a43fe0bf0bb76a5f2213e9feabe2087c3d0a31 SUCCESS
20651 0644e5a7b4dd58201c35eba9d0f8b4e7e8f8fe9c657386cb5708733fe5b1fa48 SUCCESS
20652 17036f052629bb4e8d5b983c1e38bcf3ebd18dfe74161482f4f667f115

20744 d1c3e0054f4e3af7f3c8713b62c5baeea83234987a4aaf98dab55c1f224752b4 SUCCESS
20745 7e4409eaee44962e68cef5a92e5a4f0010aa95678c96efabc694dff4245b224f SUCCESS
20746 04b6a2d104c2d9d3cafefe847269390c4c959f675e5f8934c9f4c903cf65be25 SUCCESS
20747 46a2e988ccb98a800b8f06abb1cfd01d5dbdce8d01fe5a73bbf3272f06d1d025 SUCCESS
20748 2f90dcdfcafa82b69e2d6ef381a9a98aa6504018c8d1c0a7f29d0243364c589f SUCCESS
20749 272a9f3580c7932b419347147b6806ad1bb839e3f2681a897905290130279607 SUCCESS


In [17]:
session = requests.Session()
session.auth = (user, password)
print(session.get(MAAS_ENDPOINT + "available_results").text)

[
  {
    "config": {
      "config": {
        "run_id": "fc46f7f1606b1132512814a08e7420da69e0bc27543ab0a6be245b374dff25ad"
      },
      "name": "population_model"
    },
    "output": "https://s3.amazonaws.com/world-modelers/results/population_model/fc46f7f1606b1132512814a08e7420da69e0bc27543ab0a6be245b374dff25ad.csv",
    "status": "SUCCESS"
  },
  {
    "config": {
      "config": {
        "percent_of_normal_rainfall": 1,
        "run_id": "33878c54dc45056bb2c6b83fd71c9293a128ca1f45186a85aa976d76ded1dc89"
      },
      "name": "malnutrition_model"
    },
    "output": "https://s3.amazonaws.com/world-modelers/results/malnutrition_model/33878c54dc45056bb2c6b83fd71c9293a128ca1f45186a85aa976d76ded1dc89.geojson",
    "status": "SUCCESS"
  },
  {
    "config": {
      "config": {
        "percent_of_normal_rainfall": 80,
        "run_id": "22e92d6484b3d7baf0590140d30d8fc2945c6548e83e2271fe76fbbddd6f00a2"
      },
      "name": "malnutrition_model"
    },
    "output": "https://s3.ama

In [58]:
import wget
import zipfile
import os

def prep_p(session,model_name,runs,fields):
    
    dfs = []
    for run in runs:
        mydata = {
           "config":{},
           "name":model_name
        }
        for i, field in enumerate(fields):
            mydata["config"][field] = run[i]

        URL = MAAS_ENDPOINT + "run_model"
        print(json.dumps(mydata))
        resp = session.post(URL, json=mydata)
        rid = resp.text.replace('"',"").strip()
        run_response = session.get(MAAS_ENDPOINT + "run_status/" + rid)
        STATUS = run_response.text.replace('"',"").strip()
        if STATUS == "SUCCESS":
            URL = MAAS_ENDPOINT + "run_results"
            run_response = session.get(MAAS_ENDPOINT + "run_results/" + rid)
            outloc = json.loads(run_response.text)["output"]
            wget.download(outloc,"./runs/")
            with zipfile.ZipFile("./runs/" + rid + ".zip", 'r') as zip_ref:
                zip_ref.extractall("./runs/")
            os.remove("./runs/" + rid + ".zip")
            d = pd.read_csv("./runs/single_shock_results.csv")
            for i, field in enumerate(fields):
                if field == 'country':
                    field = "qcountry"
                d[field] = run[i]
            #d.to_csv("./runs/"+rid+".csv")
            dfs.append(d)
    alldf = pd.concat(dfs,ignore_index=True)
    alldf.to_csv("./runs/fsc.csv")
            
            

In [74]:
prep_p(session,"FSC",mmatrix,["country","fractional_reserve_access","production_decrease","year"])

{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 1.1e-09, "year": 2005}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 1.1e-09, "year": 2006}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 1.1e-09, "year": 2007}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 1.1e-09, "year": 2008}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 1.1e-09, "year": 2009}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 0.25000000109, "year": 2005}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "production_decrease": 0.25000000109, "year": 2006}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.1e-09, "productio

{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.25000000109, "year": 2009}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.50000000108, "year": 2005}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.50000000108, "year": 2006}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.50000000108, "year": 2007}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.50000000108, "year": 2008}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.50000000108, "year": 2009}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.7500000010699999, "year": 2005}, "name": "FSC"}
{

{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.7500000010699999, "year": 2006}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.7500000010699999, "year": 2007}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.7500000010699999, "year": 2008}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.7500000010699999, "year": 2009}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.0000000010599999, "year": 2005}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.0000000010599999, "year": 2006}, "name": "FSC"}
{"config": {"country": "AFG", "fractional_reserve_access": 1.0000000010599999, "producti

{"config": {"country": "ALB", "fractional_reserve_access": 0.25000000109, "production_decrease": 1.0000000010599999, "year": 2009}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 1.1e-09, "year": 2005}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 1.1e-09, "year": 2006}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 1.1e-09, "year": 2007}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 1.1e-09, "year": 2008}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 1.1e-09, "year": 2009}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 0.50000000108, "production_decrease": 0.25000000109, "year": 2005}, "name": "FSC"}
{"config": {"country": "ALB", "

{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2006}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2007}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2008}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2009}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2005}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2006}, "name": "FSC"}
{"config": {"country": "ALB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "

...

{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2008}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2009}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2005}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2006}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2007}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "year": 2008}, "name": "FSC"}
{"config": {"country": "YEM", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.50000000108, "

{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.7500000010699999, "year": 2007}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.7500000010699999, "year": 2008}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.7500000010699999, "year": 2009}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 1.0000000010599999, "year": 2005}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 1.0000000010599999, "year": 2006}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 1.0000000010599999, "year": 2007}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 0.25000000109, "production_decrease": 1.0000000010599999, "

{"config": {"country": "ZMB", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 1.0000000010599999, "year": 2009}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.1e-09, "year": 2005}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.1e-09, "year": 2006}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.1e-09, "year": 2007}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.1e-09, "year": 2008}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 1.1e-09, "year": 2009}, "name": "FSC"}
{"config": {"country": "ZMB", "fractional_reserve_access": 1.0000000010599999, "production_decrease": 0.25000000109, "year": 2005}, "name": "FS

{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.25000000109, "year": 2008}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.25000000109, "year": 2009}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.50000000108, "year": 2005}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.50000000108, "year": 2006}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.50000000108, "year": 2007}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.50000000108, "year": 2008}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.25000000109, "production_decrease": 0.50000000108, "year": 2009}, "name": "FSC"}
{"conf

{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 0.7500000010699999, "year": 2005}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 0.7500000010699999, "year": 2006}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 0.7500000010699999, "year": 2007}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 0.7500000010699999, "year": 2008}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 0.7500000010699999, "year": 2009}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "production_decrease": 1.0000000010599999, "year": 2005}, "name": "FSC"}
{"config": {"country": "ZWE", "fractional_reserve_access": 0.7500000010699999, "producti